# Speech Synthesis - DevFest Nantes 2021 - IArt

 
<br>  
Brique n°4 de la conférence **IArt ou comment apprendre à une machine à tagger et à composer**
 
<br>  

<img src="images/image1.jpg" alt="Speech Synthesis" width="400px" />

### Objectifs
 
<br>  
- Faire "chanter" notre texte par une machine
<br>  
<br>  
- Mettre bout à bout nos briques et réaliser notre clip vidéo !

### Etapes

<br>  
1. Application d'un Text-To-Speech sur les paroles de notre chanson
<br>  
    - On récupère les paroles de notre chanson.
    - On applique un TTS dessus.
    - On sauvegarde le résultat pour être réutilisé dans notre clip.  
<br>  
2. Transformation du TTS
<br>  
    - On va modifier le résultat du TTS pour "dérobotiser" un peu notre chason et accélérer le rythme.  
<br>  
3. Ajout des beats
<br>  
    - Chargement de nos "beats" & de nos paroles au format audio.
    - Modification de volume et ajout d'effets.
    - Création de notre chanson final (boucle de beats + paroles).  
<br>  
4. Création du clip
<br>  
    - Chargement de notre chanson pour récupérer la durée.
    - Chargement des images et création du clip vidéo (sans l'audio).
    - Création de notre clip final (mix audio & vidéo).  
<br>  

---

### Données

<br>  
Ce notebook utilise les résultats des 3 premières briques de notre conférence.  Les résultats doivent être placés manuellement dans un dossier `./inputs` :

- **\*.png** : images de notre clip - brique n°1
    - Le nom des images va correspondre à l'ordre d'affichage dans notre clip.
    - On a légèrement modifié notre brique n°1 pour sauvegarder toutes les étapes du processus. Libre à vous de faire pareil si vous le souhaité.  
    
- **lyrics.txt** : texte de notre chason - brique n°2  

- **beats.wav** : beats de notre chason - brique n°3  


---

### Imports

In [1]:
# Divers
import os
import random
import numpy as np
import pandas as pd
from datetime import datetime
from IPython.display import display, HTML, Javascript, clear_output, Video

# Musique / TTS
import pyttsx3
import librosa
import soundfile as sf
from pydub import AudioSegment
from pydub.playback import play

# Video
from moviepy.editor import VideoFileClip, AudioFileClip, CompositeAudioClip
from moviepy.video.io.ImageSequenceClip import ImageSequenceClip

In [2]:
# Center figures
HTML("""
<style>
.output_png {
    display: table-cell;
    text-align: center;
    vertical-align: middle;
}
</style>
""")

---

### Fonctions utilitaires

<br>  
On commence par définir certaines fonctions utilitaires :

- **hide_toggle** : permet de "masquer" certaines cellules de ce notebook, ce qui permet d'apporter un peu plus de clarté ;)   

In [3]:
def hide_toggle(for_next=False, text_display='Toggle show/hide'):
    '''Function to hide a notebook cell'''
    this_cell = """$('div.cell.code_cell.rendered.selected')"""
    target_cell = this_cell  # target cell to control with toggle

    js_f_name = 'code_toggle_{}'.format(str(random.randint(1,2**64)))

    html = f"""
        <script>
            function {js_f_name}() {{
                {target_cell}.find('div.input').toggle();
            }}

        </script>

        <a href="javascript:{js_f_name}()" id="{js_f_name}">{text_display}</a>
    """
    
    js = f'''
            var output_area = this;
            var cell_element = output_area.element.parents('.cell');
            var cell_idx = Jupyter.notebook.get_cell_elements().index(cell_element);
            var current_cell = Jupyter.notebook.get_cell(cell_idx);
            $(current_cell.element[0]).find('div.input').toggle();
            Jupyter.notebook.select(cell_idx +  1);
            Jupyter.notebook.focus_cell();
         '''

    display(HTML(html))
    display(Javascript(js))

hide_toggle(text_display='Toggle show/hide --- fonction hide_toggle')

<IPython.core.display.Javascript object>

---

### 1. Application d'un Text-To-Speech sur les paroles de notre chanson

<br>

- On récupère les paroles de notre chanson.
- On applique un TTS dessus.
- On sauvegarde le résultat pour être réutilisé dans notre clip.
<br>   
<br>   

On définit quelques fonctions pour clarifier le notebook :

- **apply_tts** : Fonction pour appliquer un TTS à du texte  

In [4]:
def apply_tts(lyrics: str, output_path: str, voice_id: int = 0, voice_rate: int = 120,
              dots_strategy: str = None, dots_interval: int = 6, min_interval: int = 5, max_interval: int = 10):
    '''Fonction pour appliquer un TTS à du texte
    
    Args:
        lyrics (str): paroles à transformer en son
        output_path (str): chemin du fichier en sortie
        voice_id (int): id de la voix à utiliser
            pyttsx3 utilise les voix installées sur votre machine, vous pouvez facilement les lister:
                `
                    for voice in pyttsx3.init().getProperty('voices') :
                        print(voice.id, voice.name, voice.age, voice.gender, voice.languages, sep=' - ')
                `
        voice_rate (int): rate à utiliser pour synthétiser une voix
        dots_strategy (str): stratégie à utiliser pour la gestion des points
            None: on ne transforme pas le texte en entrée -> le texte manque de ponctuations et est lu d'une traite, résultats moyens
            'fix': on met automatiquement un point tous les "dots_interval" mots
            'random_range': on met des points "aléatoirement" entre min_interval et max_interval mots
        dots_interval (int): interval à utiliser si dots_strategy == 'fix'
        min_interval (int): interval minimal pour la stratégie 'random_range'
        max_interval (int): interval maximal pour la stratégie 'random_range'
    '''
    # On commence par modifier nos lyrics si dots_strategy != None
    
    # Point fix
    if dots_strategy == 'fix':
        lyrics = ' '.join([x if i%dots_interval != 0 or i == 0 else x + '. ' for i, x in enumerate(lyrics.split(' '))])

    # Point aléatoire dans une range donnée
    if dots_strategy == 'random_range':
        new_lyrics = ''
        words_since_dots = 0
        for word in lyrics.split(' '):
            if words_since_dots < min_interval:
                new_lyrics += word + ' '
                words_since_dots += 1
            elif words_since_dots < max_interval:
                # Même proba pour chaque interval possible
                if random.random() < 1 / (max_interval - min_interval + 1):
                    new_lyrics += word + '. '
                    words_since_dots = 0
                else:
                    new_lyrics += word + ' '
                    words_since_dots += 1
            else:
                new_lyrics += word + '. '
                words_since_dots = 0
        lyrics = new_lyrics
        
    # Initialisation du synthétiseur
    synthesizer = pyttsx3.init()
    # Récupération des voix à dispo
    voices = synthesizer.getProperty('voices')
    # Propriétés de la voix
    synthesizer.setProperty('voice', voices[voice_id].id)  # Peut crash is l'id > nb voix
    synthesizer.setProperty('rate', voice_rate)

    # Save to file
    synthesizer.save_to_file(lyrics, output_path)

    # Run
    synthesizer.runAndWait()
    synthesizer.stop()
    
hide_toggle(text_display='Toggle show/hide --- fonction apply_tts')

<IPython.core.display.Javascript object>

In [5]:
# On va créer un dossier où sauvegarder toutes nos données
subfolder_name = datetime.now().strftime(f"experimentation_%Y_%m_%d-%H_%M_%S")
os.makedirs(subfolder_name)
subfolder_path = os.path.abspath(subfolder_name)
print(f"L'ensemble des données seront sauvegardées dans le répertoire {subfolder_path}")

L'ensemble des données seront sauvegardées dans le répertoire C:\Users\Alexandre\Dev\Valeuriad\devfest-2021\04_speech-synth\experimentation_2021_10_17-17_20_18


In [6]:
# Chargement de nos paroles
lyrics_path = os.path.join('inputs', 'lyrics.txt')
with open(lyrics_path, 'r') as f:
    lyrics = f.read()

# Si on veut, on peut limiter la longueur du texte pour avoir une musique plus courte
# lyrics = lyrics[:400]

print(lyrics)

Yo, club getta gift what the fuck can I feel the fact that he was shooting can't stop We dont Whore we come up the question Verse 2 dawg New death to the road earth like a cryin to our lyrics try to plus amnesia A 747 I'm in avallest Lighthoutered rocks That reality now do you exercha You rubbed That's well he lace wit it through the low nigga I got the dirt candy off me Now rollin illest how much Given this belt end and now whether why we all aslocks they shos isn't have a 45 thank you alright he prame a baby you are unometten LIKE WHOLE I SO CROYY'S'LL TALK SMU CHOPPAPE LOVE A Fredo identiumph I'ma find a Zoe man you want to jeall legs which that notta pictures a single squad while they ain't doing you years you can't believe me by you Livin life I tell you what you can have I tell you're drunk from the slaff Niggaz Swear his prepare to respect that guy ranste Board Take my heart and slim this smarter Gill where white 'Cause you die And if instage them bitches so every chick I got so

In [7]:
# On applique le TTS

# Chemin de sortie pour l'audio
lyrics_tts_path = os.path.join(subfolder_path, 'lyrics_tts.wav')
# Plusieurs stratégies possibles pour gérer les points (i.e. ajouter de la ponctuation)
apply_tts(lyrics, lyrics_tts_path, voice_id=1, voice_rate=120, dots_strategy='fix', dots_interval=6)

In [8]:
# Résultat
AudioSegment.from_file(lyrics_tts_path)

---

### 2. Transformation du TTS

<br>

- On va modifier le résultat du TTS pour "dérobotiser" un peu notre chason et accélérer le rythme.

In [9]:
# Chemin de sortie pour l'audio
lyrics_tts_modified_path = os.path.join(subfolder_path, 'lyrics_tts_modified.wav')

# On propose 2 solutions, mais la première nous semble la plus "sympathique" à écouter

# Solution 1 :
sound = AudioSegment.from_file(lyrics_tts_path, format="wav")
octaves = 0.2
new_sample_rate = int(sound.frame_rate * (2.0 ** octaves))
hipitch_sound = sound._spawn(sound.raw_data, overrides={'frame_rate': new_sample_rate})
hipitch_sound = hipitch_sound.set_frame_rate(44100)
hipitch_sound.export(lyrics_tts_modified_path, format="wav")

# Solution 2 :
# y, sr = librosa.load(lyrics_tts_path)
# y = librosa.effects.pitch_shift(y, sr, n_steps=1)
# y = librosa.effects.time_stretch(y, 1.2)
# sf.write(lyrics_tts_modified_path, y, sr)

<_io.BufferedRandom name='C:\\Users\\Alexandre\\Dev\\Valeuriad\\devfest-2021\\04_speech-synth\\experimentation_2021_10_17-17_20_18\\lyrics_tts_modified.wav'>

In [10]:
# Résultat
AudioSegment.from_file(lyrics_tts_modified_path)

---

### 3. Ajout des beats

<br>

- Chargement de nos "beats" & de nos paroles au format audio.
- Modification de volume et ajout d'effets.
- Création de notre chanson final (boucle de beats + paroles).

In [11]:
# Chargement des "beats"
beats = AudioSegment.from_file("inputs/beats.wav")
# Chargement des paroles
lyrics_audio = AudioSegment.from_file(lyrics_tts_modified_path)

In [12]:
# On augmente le volume des beats de 18dB
beats = beats + 18

# On va jouer une première fois les beats sans paroles
silent_init = AudioSegment.silent(duration=len(beats), frame_rate=beats.frame_rate)

# On calcul le nombre de fois où on doit jouer les beats
nb_beats = (len(silent_init) + len(lyrics_audio)) // len(beats) + 1

# On ajoute du fade_in & fade_out
fade_in_duration = len(beats)
fade_out_duration = int((nb_beats - (len(silent_init) + len(lyrics_audio)) / len(beats)) * len(beats))

# On initialise la chanson avec les beats
final_song = beats * nb_beats

# On y ajoute les paroles & les effets
final_song = final_song.overlay(silent_init + lyrics_audio).fade_in(fade_in_duration).fade_out(fade_out_duration)

In [13]:
# Sauvegarde
final_song_path = os.path.join(subfolder_path, 'final_song.wav')
final_song.export(final_song_path, format='wav')

<_io.BufferedRandom name='C:\\Users\\Alexandre\\Dev\\Valeuriad\\devfest-2021\\04_speech-synth\\experimentation_2021_10_17-17_20_18\\final_song.wav'>

In [14]:
# Résultat
AudioSegment.from_file(final_song_path)

---

### 4. Création du clip

<br>

- Chargement de notre chanson pour récupérer la durée.
- Chargement des images et création du clip vidéo (sans l'audio).
- Création de notre clip final (mix audio & vidéo).

In [15]:
# Chargement de notre chanson
final_song = AudioSegment.from_file(final_song_path)

# Durée en seconds
duration_in_seconds = len(final_song) / 1000

In [16]:
# Chargement des images
inputs_folder = os.path.abspath('inputs')
image_files = [os.path.join(inputs_folder, img) for img in os.listdir(inputs_folder) if img.endswith(".png")]

# On définit le nombre d'images par second en fonction de la durée de la chanson et du nombre d'images à afficher
fps = len(image_files) / duration_in_seconds
print(f"On affiche {fps} images par seconde")

# Création de notre video (sans son)

# Si vous obtenez une erreur " TypeError: must be real number, not NoneType " :
#     Vous pouvez éditer le fichier config_defaults.py présent dans la répertoire d'installation de moviepy (dans votre venv)
#     et modifier la valeur de FFMPEG_BINARY par le chemin direct du fichier ffmpeg.exe
clip = ImageSequenceClip(image_files, fps=fps)
clip.write_videofile(os.path.join(subfolder_path, 'tmp_video.mp4'), fps=fps)

On affiche 0.10148444059008589 images par seconde
Moviepy - Building video C:\Users\Alexandre\Dev\Valeuriad\devfest-2021\04_speech-synth\experimentation_2021_10_17-17_20_18\tmp_video.mp4.
Moviepy - Writing video C:\Users\Alexandre\Dev\Valeuriad\devfest-2021\04_speech-synth\experimentation_2021_10_17-17_20_18\tmp_video.mp4



Moviepy - Done !
Moviepy - video ready C:\Users\Alexandre\Dev\Valeuriad\devfest-2021\04_speech-synth\experimentation_2021_10_17-17_20_18\tmp_video.mp4


In [17]:
# On recharge video & audio
videoclip = VideoFileClip(os.path.join(subfolder_path, 'tmp_video.mp4'))
audioclip = AudioFileClip(final_song_path)

# On mix les deux
videoclip.audio = CompositeAudioClip([audioclip])

# On sauvegarde le résultat final !
final_clip_path = os.path.join(subfolder_path, 'final_clip.mp4')
videoclip.write_videofile(final_clip_path)

Moviepy - Building video C:\Users\Alexandre\Dev\Valeuriad\devfest-2021\04_speech-synth\experimentation_2021_10_17-17_20_18\final_clip.mp4.
MoviePy - Writing audio in final_clipTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video C:\Users\Alexandre\Dev\Valeuriad\devfest-2021\04_speech-synth\experimentation_2021_10_17-17_20_18\final_clip.mp4



Moviepy - Done !
Moviepy - video ready C:\Users\Alexandre\Dev\Valeuriad\devfest-2021\04_speech-synth\experimentation_2021_10_17-17_20_18\final_clip.mp4


In [18]:
# Affichage
Video(final_clip_path, embed=True)